In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/dataset0001/Sentence pairs in English-Hindi - 2025-02-11.tsv


In [4]:
from transformers import AutoTokenizer #for english tokenization
import torch
import torch.nn.functional as F

In [5]:
!pip3 install indic-nlp-library

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 2.2 MB/s eta 0:00:00


In [6]:
from indicnlp.tokenize import indic_tokenize #hindi tokenization built by AI for Bharat

In [7]:
data=pd.read_csv("/kaggle/input/dataset0001/Sentence pairs in English-Hindi - 2025-02-11.tsv",sep="\t",header=None,names=["SrcSentID","SrcSent","DstSentID","DstSent"])

In [8]:
data.head()

SrcSentID                                  SrcSent  DstSentID  \
0       1282                       Muiriel is 20 now.     485968   
1       1282                       Muiriel is 20 now.    2060319   
2       1294  Education in this world disappoints me.     485564   
3       1302                       That won't happen.    2060320   
4       1308                              I miss you.    2060321   

                                       DstSent  
0             म्यूरियल अब बीस साल की हो गई है।  
1                   म्यूरियल अब बीस साल की है।  
2  मैं इस दुनिया में शिक्षा पर बहुत निराश हूँ।  
3                              वैसा नहीं होगा।  
4                 मुझें तुम्हारी याद आ रही है।

In [9]:
data.shape

(13182, 4)

In [10]:
data.drop(labels=[data.columns[0],data.columns[2]],axis=1,inplace=True)

In [11]:
data.head()

SrcSent  \
0                       Muiriel is 20 now.   
1                       Muiriel is 20 now.   
2  Education in this world disappoints me.   
3                       That won't happen.   
4                              I miss you.   

                                       DstSent  
0             म्यूरियल अब बीस साल की हो गई है।  
1                   म्यूरियल अब बीस साल की है।  
2  मैं इस दुनिया में शिक्षा पर बहुत निराश हूँ।  
3                              वैसा नहीं होगा।  
4                 मुझें तुम्हारी याद आ रही है।

In [12]:
src_sent_tokenizer=AutoTokenizer.from_pretrained("google-T5/T5-base") #T5 is an llm deloped by google,and hum T5 ka base model use karengey, har llm ka apna khud ka tokenizer hota hai
#hugging face me gogle-T5 repository me T5-base model import kar rahe hai


config.json: 0.00B [00:00, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [13]:
data.head()

SrcSent  \
0                       Muiriel is 20 now.   
1                       Muiriel is 20 now.   
2  Education in this world disappoints me.   
3                       That won't happen.   
4                              I miss you.   

                                       DstSent  
0             म्यूरियल अब बीस साल की हो गई है।  
1                   म्यूरियल अब बीस साल की है।  
2  मैं इस दुनिया में शिक्षा पर बहुत निराश हूँ।  
3                              वैसा नहीं होगा।  
4                 मुझें तुम्हारी याद आ रही है।

In [14]:
data["SrcSent"]=data["SrcSent"].apply(lambda x:src_sent_tokenizer.tokenize(x))
#apply
#applyMap
#Map

In [15]:
data.head()
#there are two types of algorithm used to tokenize
#1. Byte-Pair Encoding(BPE) Tokenizer
#2. Word Piece Tokenizer(WPT)

SrcSent  \
0                  [▁Mu, i, riel, ▁is, ▁20, ▁now, .]   
1                  [▁Mu, i, riel, ▁is, ▁20, ▁now, .]   
2  [▁Education, ▁in, ▁this, ▁world, ▁disappoint, ...   
3                    [▁That, ▁won, ', t, ▁happen, .]   
4                               [▁I, ▁miss, ▁you, .]   

                                       DstSent  
0             म्यूरियल अब बीस साल की हो गई है।  
1                   म्यूरियल अब बीस साल की है।  
2  मैं इस दुनिया में शिक्षा पर बहुत निराश हूँ।  
3                              वैसा नहीं होगा।  
4                 मुझें तुम्हारी याद आ रही है।

In [16]:
data["DstSent"]=data["DstSent"].apply(lambda x:indic_tokenize.trivial_tokenize(x,lang="hi"))

In [17]:
data.head()

SrcSent  \
0                  [▁Mu, i, riel, ▁is, ▁20, ▁now, .]   
1                  [▁Mu, i, riel, ▁is, ▁20, ▁now, .]   
2  [▁Education, ▁in, ▁this, ▁world, ▁disappoint, ...   
3                    [▁That, ▁won, ', t, ▁happen, .]   
4                               [▁I, ▁miss, ▁you, .]   

                                             DstSent  
0        [म्यूरियल, अब, बीस, साल, की, हो, गई, है, ।]  
1                [म्यूरियल, अब, बीस, साल, की, है, ।]  
2  [मैं, इस, दुनिया, में, शिक्षा, पर, बहुत, निराश...  
3                              [वैसा, नहीं, होगा, ।]  
4              [मुझें, तुम्हारी, याद, आ, रही, है, ।]

In [18]:
data["SrcSent"]=data["SrcSent"].apply(src_sent_tokenizer.convert_tokens_to_ids)

In [19]:
data.head()

SrcSent  \
0     [4159, 23, 14018, 19, 460, 230, 5]   
1     [4159, 23, 14018, 19, 460, 230, 5]   
2  [2855, 16, 48, 296, 26963, 7, 140, 5]   
3            [466, 751, 31, 17, 1837, 5]   
4                      [27, 3041, 25, 5]   

                                             DstSent  
0        [म्यूरियल, अब, बीस, साल, की, हो, गई, है, ।]  
1                [म्यूरियल, अब, बीस, साल, की, है, ।]  
2  [मैं, इस, दुनिया, में, शिक्षा, पर, बहुत, निराश...  
3                              [वैसा, नहीं, होगा, ।]  
4              [मुझें, तुम्हारी, याद, आ, रही, है, ।]

In [20]:
vs=src_sent_tokenizer.get_vocab()

In [21]:
len(vs)

32100

In [22]:
hindi_vocab=set()
for tokenized_hindi_sent in data["DstSent"]:
    hindi_vocab.update(tokenized_hindi_sent)

In [23]:
len(hindi_vocab)

7069

In [24]:
#we have to define three extra tokens "<SOS">=start of sentence =token(1) ,"PAD"=padding(to get each sentence of same length to make a matrix) =pad token(0),"EOS"=end of sentence =token(2)


In [25]:
vd=dict() 
for idx,token in enumerate(hindi_vocab):
    vd[token]=idx+3
vd["<PAD>"]=0
vd["<SOS>"]=1
vd["<EOS>"]=2

In [26]:
hindi_idx2vocab=dict(zip(vd.values(),vd.keys()))
print(hindi_idx2vocab)

{3: 'पैरिस', 4: 'ऊँचाई', 5: 'घूँसा', 6: 'धुंध', 7: 'बाथरूम', 8: 'पोतियां', 9: 'मिटती', 10: '१९९२', 11: 'ज़ुबान', 12: 'एलिस', 13: 'लगा', 14: 'मॅरी', 15: 'ज़िम्मेदार', 16: 'पकड़ा', 17: 'लगकर', 18: 'चलाना', 19: 'चाहिएं', 20: 'अस्सी', 21: 'ज्ञात', 22: 'दर', 23: 'नक़्शे', 24: 'बॉयफ़्रेंड', 25: 'जैन', 26: 'दंभी', 27: 'मंगोलीयाई', 28: 'अरब', 29: 'आवाज़ें', 30: 'उत्तम', 31: 'टुकड़ों', 32: 'लंबे', 33: 'आश्चर्यचकित', 34: 'वापस', 35: 'मुड़ना', 36: 'बुलवाई', 37: 'टिकती', 38: 'मानचित्र', 39: 'मुझ', 40: 'पहने', 41: 'एवरेस्ट', 42: 'हाय', 43: 'वस्तु', 44: 'चश्मदीद', 45: 'रूप', 46: 'फ़ोटो', 47: 'प्रकट', 48: 'पेट', 49: 'शुक्रवार', 50: 'ग़लतियाँ', 51: 'स्टार', 52: 'राजनीति', 53: 'एम्पायर', 54: 'बढ़ती', 55: 'कम्प्यूटर', 56: 'क्योतो', 57: 'बसे', 58: 'पहनती', 59: 'बिज्जू', 60: 'ऊष्मा', 61: '४०००', 62: '१०', 63: 'ड्रैगन्स', 64: 'नेपाली', 65: 'परिस्तिथि', 66: 'अफ़सर', 67: 'कपों', 68: 'साली', 69: 'पतला', 70: 'मशहूर', 71: 'दुर्प्रभावों', 72: 'समझाया', 73: 'पूछने', 74: 'दफ़नाया', 75: 'खुशमिज़ाज', 76: 'बजती', 77:

In [27]:
# print(vd)
len(vd)

7072

In [28]:
def convert_hindi_tokens_to_ids(hindi_sent):
    return [vd[token] for token in hindi_sent]

In [29]:
data["DstSent"]=data["DstSent"].apply(lambda x:convert_hindi_tokens_to_ids(x))

In [30]:
data.head()

SrcSent  \
0     [4159, 23, 14018, 19, 460, 230, 5]   
1     [4159, 23, 14018, 19, 460, 230, 5]   
2  [2855, 16, 48, 296, 26963, 7, 140, 5]   
3            [466, 751, 31, 17, 1837, 5]   
4                      [27, 3041, 25, 5]   

                                             DstSent  
0  [3335, 3786, 4712, 6120, 4371, 5964, 4533, 611...  
1         [3335, 3786, 4712, 6120, 4371, 6115, 4457]  
2  [5304, 6220, 3144, 2353, 2401, 4035, 5424, 211...  
3                            [438, 6312, 2952, 4457]  
4         [1607, 5666, 6521, 4873, 6343, 6115, 4457]

In [31]:
def insert_sos_token_id(hindi_sent_token_ids):
    return [1]+hindi_sent_token_ids

In [32]:
data["DstSentInput"]=data["DstSent"].apply(lambda x:insert_sos_token_id(x))

In [33]:
data.head()

SrcSent  \
0     [4159, 23, 14018, 19, 460, 230, 5]   
1     [4159, 23, 14018, 19, 460, 230, 5]   
2  [2855, 16, 48, 296, 26963, 7, 140, 5]   
3            [466, 751, 31, 17, 1837, 5]   
4                      [27, 3041, 25, 5]   

                                             DstSent  \
0  [3335, 3786, 4712, 6120, 4371, 5964, 4533, 611...   
1         [3335, 3786, 4712, 6120, 4371, 6115, 4457]   
2  [5304, 6220, 3144, 2353, 2401, 4035, 5424, 211...   
3                            [438, 6312, 2952, 4457]   
4         [1607, 5666, 6521, 4873, 6343, 6115, 4457]   

                                        DstSentInput  
0  [1, 3335, 3786, 4712, 6120, 4371, 5964, 4533, ...  
1      [1, 3335, 3786, 4712, 6120, 4371, 6115, 4457]  
2  [1, 5304, 6220, 3144, 2353, 2401, 4035, 5424, ...  
3                         [1, 438, 6312, 2952, 4457]  
4      [1, 1607, 5666, 6521, 4873, 6343, 6115, 4457]

In [34]:
def insert_eos_token_id(hindi_sent_token_ids):
    return hindi_sent_token_ids+[2]

In [35]:
data["DstSentLabel"]=data["DstSent"].apply(lambda x:insert_eos_token_id(x))

In [36]:
data.head()

SrcSent  \
0     [4159, 23, 14018, 19, 460, 230, 5]   
1     [4159, 23, 14018, 19, 460, 230, 5]   
2  [2855, 16, 48, 296, 26963, 7, 140, 5]   
3            [466, 751, 31, 17, 1837, 5]   
4                      [27, 3041, 25, 5]   

                                             DstSent  \
0  [3335, 3786, 4712, 6120, 4371, 5964, 4533, 611...   
1         [3335, 3786, 4712, 6120, 4371, 6115, 4457]   
2  [5304, 6220, 3144, 2353, 2401, 4035, 5424, 211...   
3                            [438, 6312, 2952, 4457]   
4         [1607, 5666, 6521, 4873, 6343, 6115, 4457]   

                                        DstSentInput  \
0  [1, 3335, 3786, 4712, 6120, 4371, 5964, 4533, ...   
1      [1, 3335, 3786, 4712, 6120, 4371, 6115, 4457]   
2  [1, 5304, 6220, 3144, 2353, 2401, 4035, 5424, ...   
3                         [1, 438, 6312, 2952, 4457]   
4      [1, 1607, 5666, 6521, 4873, 6343, 6115, 4457]   

                                        DstSentLabel  
0  [3335, 3786, 4712, 6120, 4371, 5964, 4533, 611...  
1      [3335, 3786, 4712, 6120, 4371, 6115, 4457, 2]  
2  [5304, 6220, 3144, 2353, 2401, 4035, 5424, 211...  
3                         [438, 6312, 2952, 4457, 2]  
4      [1607, 5666, 6521, 4873, 6343, 6115, 4457, 2]

In [37]:
#max dimension of a word embedding is 4096 and min is 32 ,it affects the size of the llms,it increases in the power of 2

In [38]:
data.drop(labels=[data.columns[1]],axis=1,inplace=True)

In [39]:
#Ragged array: har row ke liye different number of columns hoga
x=list(data["SrcSent"])#without padding ye ek ragged array ban sakta hai
y_input=list(data["DstSentInput"])
y_label=list(data["DstSentLabel"])

In [40]:
x_tensor=[torch.tensor(tokenized_eng_sent_ids) for tokenized_eng_sent_ids in x]
y_input_tensor=[torch.tensor(tokenized_hin_sent_ids) for tokenized_hin_sent_ids in y_input]
y_label_tensor=[torch.tensor(tokenized_hin_sent_ids) for tokenized_hin_sent_ids in y_label]

In [41]:
x_padded=torch.nn.utils.rnn.pad_sequence(x_tensor,batch_first=True)
y_padded_input=torch.nn.utils.rnn.pad_sequence(y_input_tensor,batch_first=True)
y_padded_label=torch.nn.utils.rnn.pad_sequence(y_label_tensor,batch_first=True)

In [42]:
ns=x_padded.shape[1]
nd=y_padded_label.shape[1]

In [43]:
ns

68

In [44]:
nd #ye coincidence hai ki ns or nd barabar aa rahe hai warna jaruri nahi hai ki humesha barabar aaye

68

In [45]:
class Encoder(torch.nn.Module):

    def __init__(self,src_lang_vocab_size,word_embedding_dim):
        super(Encoder,self).__init__()
        self.first_embedding_layer=torch.nn.Embedding(num_embeddings=src_lang_vocab_size,
                                                     embedding_dim=word_embedding_dim)
        self.second_lstm_layer=torch.nn.LSTM(input_size=word_embedding_dim,
                                             hidden_size=word_embedding_dim,
                                            batch_first=True)

    def forward(self,x_padded_mini_batch): #is function ka naam forward hi rakhna hoga kyoki ye module class ka hai
        first_embedding_layer_out=self.first_embedding_layer(x_padded_mini_batch)
        encoder_output,(final_encoder_output,final_cell_state)=self.second_lstm_layer(first_embedding_layer_out)

        return encoder_output,(final_encoder_output,final_cell_state)

In [46]:
class Decoder(torch.nn.Module):

    def __init__(self, dst_lang_vocab_size, word_embedding_dim):
        super(Decoder, self).__init__()
        
        self.first_embedding_layer = torch.nn.Embedding(
            num_embeddings=dst_lang_vocab_size,
            embedding_dim=word_embedding_dim
        )
        self.second_lstm_layer = torch.nn.LSTM(
            input_size=word_embedding_dim,
            hidden_size=word_embedding_dim,
            batch_first=True
        )
        self.prediction_layer = torch.nn.Linear(
            in_features=word_embedding_dim,
            out_features=dst_lang_vocab_size
        )

    def forward(self, y_padded_input_mini_batch, final_encoder_output, final_cell_state):

        first_embedding_layer_out = self.first_embedding_layer(y_padded_input_mini_batch)
        decoder_lstm_layer_out, (final_decoder_lstm_layer_out, final_cell_state) = self.second_lstm_layer(
            first_embedding_layer_out,
            (final_encoder_output, final_cell_state)
        )
        prediction = self.prediction_layer(decoder_lstm_layer_out)
        return prediction, (final_decoder_lstm_layer_out, final_cell_state)


In [47]:
class Seq2SeqEncDec(torch.nn.Module):

    def __init__(self,src_lang_vocab_size,dst_lang_vocab_size,word_embedding_dim):
        super(Seq2SeqEncDec,self).__init__()

        self.encoder=Encoder(src_lang_vocab_size,word_embedding_dim)
        self.decoder=Decoder(dst_lang_vocab_size,word_embedding_dim)

    def forward(self,x_padded_mini_batch,y_padded_input_mini_batch):

        encoder_output,(final_encoder_output,final_cell_state)=self.encoder(x_padded_mini_batch)
        y_hat_mini_batch=self.decoder(y_padded_input_mini_batch,
                                      final_encoder_output,final_cell_state)

        return y_hat_mini_batch

In [48]:
#to check our device has a access of gpu or not in this case we use kaggle gpu
if torch.cuda.is_available():
    device=torch.device("cuda")
else:
    device=torch.device("cpu")
print(device)

cuda


In [49]:
x_padded_train=x_padded[0:13000]
y_padded_input_train=y_padded_input[0:13000]
y_padded_label_train=y_padded_label[0:13000]

x_padded_test=x_padded[13000:]
y_padded_input_test=y_padded_input[13000:]
y_padded_label_test=y_padded_label[13000: ]

In [50]:
network = Seq2SeqEncDec(len(vs),len(vd),128).to(device)
loss_fn = torch.nn.CrossEntropyLoss(ignore_index=0)
optimizer = torch.optim.Adam(network.parameters())
num_epochs = 500
mb_size = 65

for epoch in range(num_epochs):
    for i in range(x_padded_train.shape[0]//mb_size):

        x_train_mb = x_padded_train[i*mb_size:(i+1)*mb_size]
        y_input_mb = y_padded_input_train[i*mb_size:(i+1)*mb_size]
        y_label_mb = y_padded_label_train[i*mb_size:(i+1)*mb_size]
        y_label_mb = y_label_mb.reshape(y_label_mb.shape[0]*y_label_mb.shape[1],)
        
        x_train_mb, y_input_mb, y_label_mb = x_train_mb.to(device), y_input_mb.to(device), y_label_mb.to(device)

        y_hat_train_mb = network(x_train_mb,y_input_mb)
        y_hat_train_mb = y_hat_train_mb[0]
        y_hat_train_mb = y_hat_train_mb.reshape(y_hat_train_mb.shape[0]*y_hat_train_mb.shape[1],
                                                y_hat_train_mb.shape[2])

        loss_fn_value = loss_fn(y_hat_train_mb,y_label_mb)

        loss_fn_value.backward()
        torch.nn.utils.clip_grad_norm_(network.parameters(),max_norm=1.0)
        optimizer.step()
        optimizer.zero_grad()

        print("Epoch # {}, Time Step # {}, Loss Value = {}".format(epoch,i,loss_fn_value))

Epoch # 0, Time Step # 0, Loss Value = 8.83283519744873
Epoch # 0, Time Step # 1, Loss Value = 8.825705528259277
Epoch # 0, Time Step # 2, Loss Value = 8.789473533630371
Epoch # 0, Time Step # 3, Loss Value = 8.762385368347168
Epoch # 0, Time Step # 4, Loss Value = 8.73204231262207
Epoch # 0, Time Step # 5, Loss Value = 8.683308601379395
Epoch # 0, Time Step # 6, Loss Value = 8.66146469116211
Epoch # 0, Time Step # 7, Loss Value = 8.605682373046875
Epoch # 0, Time Step # 8, Loss Value = 8.583956718444824
Epoch # 0, Time Step # 9, Loss Value = 8.504266738891602
Epoch # 0, Time Step # 10, Loss Value = 8.41124153137207
Epoch # 0, Time Step # 11, Loss Value = 8.345423698425293
Epoch # 0, Time Step # 12, Loss Value = 8.123437881469727
Epoch # 0, Time Step # 13, Loss Value = 8.169901847839355
Epoch # 0, Time Step # 14, Loss Value = 7.9580512046813965
Epoch # 0, Time Step # 15, Loss Value = 7.867465972900391
Epoch # 0, Time Step # 16, Loss Value = 7.622438430786133
Epoch # 0, Time Step # 17, 

In [54]:
torch.save(network.state_dict(),"model.pth")

# INFERENCE LOGIC

In [55]:
def generate_translation(eng_sentence):

    tokenized_eng_sentence = src_sent_tokenizer.tokenize(eng_sentence)
    token_ids = src_sent_tokenizer.convert_tokens_to_ids(tokenized_eng_sentence)
    token_ids_tensor = torch.tensor(token_ids)
    token_ids_tensor = torch.unsqueeze(token_ids_tensor,0)

    if torch.cuda.is_available():
        device = torch.device("cuda")
        token_ids_tensor = token_ids_tensor.to(device)

    encoder_outputs,(final_encoder_output,final_candidate_cell_state) = network.encoder(token_ids_tensor)
    decoder_first_time_step_input = torch.tensor([[1]])

    if torch.cuda.is_available():
        encoder_outputs = encoder_outputs.to(device)
        final_encoder_output = final_encoder_output.to(device)
        final_candidate_cell_state = final_candidate_cell_state.to(device)
        decoder_first_time_step_input = decoder_first_time_step_input.to(device)

    decoder_first_time_step_output, (hidden_decoder_output, hidden_decoder_cell_state) = network.decoder(decoder_first_time_step_input,
                                                                                                        final_encoder_output,
                                                                                                        final_candidate_cell_state)

    generated_token_id = torch.argmax(F.softmax(decoder_first_time_step_output[:,0,:],dim=1),1)
    generated_token_id = torch.unsqueeze(generated_token_id,1)

    hindi_translated_sentence = str()
    hindi_translated_sentence += " " + hindi_idx2vocab[generated_token_id.item()]

    if torch.cuda.is_available():
        generated_token_id = generated_token_id.to(device)
        hidden_decoder_output = hidden_decoder_output.to(device)
        hidden_decoder_cell_state = hidden_decoder_cell_state.to(device)
        
    for i in range(nd-1):
        
        decoder_first_time_step_output, (hidden_decoder_output, hidden_decoder_cell_state) = network.decoder(generated_token_id,
                                                                                                hidden_decoder_output,
                                                                                                hidden_decoder_cell_state)
        generated_token_id = torch.argmax(F.softmax(decoder_first_time_step_output[:,0,:],dim=1),1)
        generated_token_id = torch.unsqueeze(generated_token_id,1)

        if torch.cuda.is_available():
            generated_token_id = generated_token_id.to(device)
            hidden_decoder_output = hidden_decoder_output.to(device)
            hidden_decoder_cell_state = hidden_decoder_cell_state.to(device)

        if generated_token_id.item() == vd["<EOS>"]:
            break

        hindi_translated_sentence += " " + hindi_idx2vocab[generated_token_id.item()]

    return hindi_translated_sentence

In [56]:
generate_translation("hello")

' : छाते स्थिति आश्चर्य सम्मेलन कहावत बोतल नौ ।'